In [1]:
from non_dominated_sort import fast_non_dominated_sort as fnds
from non_dominated_sort import dominance_check_between_two_points as dc
from non_dominated_sort import insert as insert
from non_dominated_sort import non_dominated_sorting as nds
from fitness_calculation import calculate_error_rate as error
from one_bit_purifying_search import one_bit_purifying_search as obps

In [2]:
import pandas as pd
import io
from sklearn.model_selection import train_test_split
import random
from sklearn import preprocessing

import math
from operator import itemgetter

In [3]:
from pymoo.indicators.hv import HV
import statistics

In [4]:
pd.set_option("display.max_columns",100)

In [5]:
#colnames = ['A1', 'A2', 'A3', 'A4', 'A5', 'A6', 'A7', 'A8', 'A9', 'A10', 'A11', 'A12', 'A13', 'A14', 'A15']
df = pd.read_excel('default of credit card clients.xls', sheet_name = 'Data', header=1)
#df_test = pd.read_csv('test.csv', sep=',', encoding='utf-8', index_col=False)
df.head()

ID  LIMIT_BAL  SEX  EDUCATION  MARRIAGE  AGE  PAY_0  PAY_2  PAY_3  PAY_4  \
0   1      20000    2          2         1   24      2      2     -1     -1   
1   2     120000    2          2         2   26     -1      2      0      0   
2   3      90000    2          2         2   34      0      0      0      0   
3   4      50000    2          2         1   37      0      0      0      0   
4   5      50000    1          2         1   57     -1      0     -1      0   

   PAY_5  PAY_6  BILL_AMT1  BILL_AMT2  BILL_AMT3  BILL_AMT4  BILL_AMT5  \
0     -2     -2       3913       3102        689          0          0   
1      0      2       2682       1725       2682       3272       3455   
2      0      0      29239      14027      13559      14331      14948   
3      0      0      46990      48233      49291      28314      28959   
4      0      0       8617       5670      35835      20940      19146   

   BILL_AMT6  PAY_AMT1  PAY_AMT2  PAY_AMT3  PAY_AMT4  PAY_AMT5  PAY_AMT6  \
0          0         0       689         0         0         0         0   
1       3261         0      1000      1000      1000         0      2000   
2      15549      1518      1500      1000      1000      1000      5000   
3      29547      2000      2019      1200      1100      1069      1000   
4      19131      2000     36681     10000      9000       689       679   

   default payment next month  
0                           1  
1                           1  
2                           0  
3                           0  
4                           0

In [6]:
df.shape

(30000, 25)

In [7]:
# df = df.drop('Unnamed: 0', axis=1)
# df_test = df_test.drop('Unnamed: 0', axis=1)
# df.head(2)

In [8]:
df.shape

(30000, 25)

In [9]:
df['target'] = df['default payment next month']
df = df.drop(['default payment next month'], axis=1)
df = df.drop(['ID'], axis=1)

In [10]:
# df_test['target'] = df_test['Creditability']
# df_test = df_test.drop(['Creditability'], axis=1)

In [11]:
print(df.shape)
#print(df_test.shape)

(30000, 24)


In [12]:
df['target'].value_counts()

target
0    23364
1     6636
Name: count, dtype: int64

In [13]:
#df_test['target'].value_counts()

In [14]:
df.head(1)

LIMIT_BAL  SEX  EDUCATION  MARRIAGE  AGE  PAY_0  PAY_2  PAY_3  PAY_4  \
0      20000    2          2         1   24      2      2     -1     -1   

   PAY_5  PAY_6  BILL_AMT1  BILL_AMT2  BILL_AMT3  BILL_AMT4  BILL_AMT5  \
0     -2     -2       3913       3102        689          0          0   

   BILL_AMT6  PAY_AMT1  PAY_AMT2  PAY_AMT3  PAY_AMT4  PAY_AMT5  PAY_AMT6  \
0          0         0       689         0         0         0         0   

   target  
0       1

# Creating dummy variables

In [15]:
# train_up = pd.get_dummies(df, columns = ['Account.Balance', 'Payment.Status.of.Previous.Credit', 'Purpose', 'Sex...Marital.Status', 'Guarantors', 'Most.valuable.available.asset', 'Concurrent.Credits', 'Type.of.apartment', 'Occupation', 'Foreign.Worker', 'Telephone'], drop_first= True)
# test_up = pd.get_dummies(df_test, columns = ['Account.Balance', 'Payment.Status.of.Previous.Credit', 'Purpose', 'Sex...Marital.Status', 'Guarantors', 'Most.valuable.available.asset', 'Concurrent.Credits', 'Type.of.apartment', 'Occupation', 'Foreign.Worker', 'Telephone'], drop_first= True)


In [16]:
# print(train_up.shape)
# print(test_up.shape)

In [17]:
# train_up_null_count = train_up.isna().sum()
# train_up_null_count = train_up_null_count[train_up_null_count>0]
# train_up_null_count

In [18]:
# train_up = train_up.dropna()

In [19]:
# train_up.shape

In [20]:
# train_up.head(1)

In [21]:
# test_up_null_count = test_up.isna().sum()
# test_up_null_count = test_up_null_count[test_up_null_count>0]
# test_up_null_count

In [22]:
# test_up = test_up.dropna()

In [23]:
# test_up.shape

In [24]:
# test_up.head(1)

# Creating training test split

In [25]:
X = df.drop('target', axis=1)
y = df['target']

In [26]:
X_train, X_test, y_train, y_test = train_test_split(X,y , random_state=42,  test_size=0.30,  shuffle=True) 

In [27]:
# X_train = train_up.drop('target', axis=1)
# y_train = df['target']

# X_test = test_up.drop('target', axis=1)
# y_test = df_test['target']

In [28]:
X_test.columns

Index(['LIMIT_BAL', 'SEX', 'EDUCATION', 'MARRIAGE', 'AGE', 'PAY_0', 'PAY_2',
       'PAY_3', 'PAY_4', 'PAY_5', 'PAY_6', 'BILL_AMT1', 'BILL_AMT2',
       'BILL_AMT3', 'BILL_AMT4', 'BILL_AMT5', 'BILL_AMT6', 'PAY_AMT1',
       'PAY_AMT2', 'PAY_AMT3', 'PAY_AMT4', 'PAY_AMT5', 'PAY_AMT6'],
      dtype='object')

In [29]:
X_train.shape

(21000, 23)

In [30]:
X_test.shape

(9000, 23)

In [31]:
y_train.value_counts()

target
0    16324
1     4676
Name: count, dtype: int64

In [32]:
y_test.value_counts()

target
0    7040
1    1960
Name: count, dtype: int64

In [33]:
def select_population_for_next_gen(population_size, P_t_plus_1_vector_fitness): 
    print("population_size" + str(population_size))
    print("len of P_t_plus_1_vector_fitness" + str(len(P_t_plus_1_vector_fitness)))
    P_t_plus_1 =  list(map(itemgetter(0), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = list(map(itemgetter (1,2), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = [list (item) for item in P_t_plus_1_fitness]
    
    sorted_index, sorted_values = fnds(data = P_t_plus_1_fitness)
    print("sorted_index")
    print(sorted_index)
    index_to_go_for_next_gen  = []
    
    for i in range(len(sorted_index)-1):
        if (len(sorted_index[i]) <= population_size - len(index_to_go_for_next_gen)):
            print("first if")
            print(len(sorted_index[i]))
            print(population_size - len(index_to_go_for_next_gen))
            index_to_go_for_next_gen = index_to_go_for_next_gen + sorted_index[i] 
        elif(len(index_to_go_for_next_gen) < population_size):
            places_left = population_size - len(index_to_go_for_next_gen)
            print("places_left")
            print(places_left)
            index_to_go_for_next_gen = index_to_go_for_next_gen + sorted_index[i][0:places_left] 
        else:
            print("neithr if")
    print("vedved index_to_go_for_next_gen")
    print(index_to_go_for_next_gen)
    population_for_next_gen = [P_t_plus_1_vector_fitness[i] for i in index_to_go_for_next_gen] 
    print("loop population_for_next_gen")
    print(population_for_next_gen)
    return population_for_next_gen

In [34]:
def top_front(P_t_plus_1_vector_fitness): 
    print("P_t_plus_1_vector_fitness")
    print(P_t_plus_1_vector_fitness)
    P_t_plus_1 = list(map(itemgetter(0), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = list(map(itemgetter(1,2), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = [list(item) for item in P_t_plus_1_fitness]
    
    print("P_t_plus_1_fitness")
    print(P_t_plus_1_fitness)
    print("before fnds")
    sorted_index, sorted_values = fnds(data = P_t_plus_1_fitness)
    print("after fnds")
    sorted_first_front_by_error = sorted(sorted_values[0], key = lambda x: x[0], reverse=True) 
    index_of_minimum_error_element = sorted_index[0][sorted_values[0].index(sorted_first_front_by_error[0])] 
     
    top_front = [P_t_plus_1[i] for i in sorted_index[0]]
    optimal_sol =  P_t_plus_1[index_of_minimum_error_element]
       
    return top_front

In [35]:
def optimal_sol(P_t_plus_1_vector_fitness): 
    P_t_plus_1 = list(map(itemgetter(0), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = list(map(itemgetter(1,2), P_t_plus_1_vector_fitness))
    P_t_plus_1_fitness = [list(item) for item in P_t_plus_1_fitness]
    
    sorted_index, sorted_values = fnds(data = P_t_plus_1_fitness)
    sorted_first_front_by_error = sorted(sorted_values[0], key = lambda x: x[0], reverse=True) 
    index_of_minimum_error_element = sorted_index[0][sorted_values[0].index(sorted_first_front_by_error[0])] 
    
    top_front = [P_t_plus_1[i] for i in sorted_index[0]]
    optimal_sol =  P_t_plus_1[index_of_minimum_error_element]
    optimal_sol_fitness =  P_t_plus_1_fitness[index_of_minimum_error_element]
    
    return optimal_sol, optimal_sol_fitness

In [36]:
def MOFS(gen_max, obps_freq, dataset_train, target_train, dataset_test, target_test, initial_population):
    P_0 = initial_population
    all_gen_population_and_fitness = []
    num_feature = 23
    
    HV_list = []
    ref_point = np.array([23,1])
    mean_hv_of_prev_10_gen_list=[]
    difference_of_current_hv_and_mean_last_10_gen_list = []
    converged = False
    
    for t in (range(gen_max)):
        print("Attention - Generation " +str(t+1) + " starts")
        P_t_plus_1 = []
        P_t_plus_1_vector_fitness = []
        P_t_plus_1_vector = []
        P_t_plus_1_fitness = []
        round_robin_flag = 0
        N = len(P_0)
        print("NNNNNNNNNNNNNNNNNNNNNN")
        print(N)
        
        for i in range(1,N+1):
            random.seed(t+30*i)
            r1, r2, r3 = random.sample(range(0,N), 3)
            print(r1, r2, r3)
            print(P_0[r1],P_0[r2],P_0[r3])
            X_r1, num_feature_r1, f1_score_r1 = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = P_0[r1])
            X_r2, num_feature_r2, f1_score_r2 = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = P_0[r2])
            X_r3, num_feature_r3, f1_score_r3 = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = P_0[r3])
            
            Dict_vector_cardinality_accuracy = {(num_feature_r1, f1_score_r1):X_r1, (num_feature_r2, f1_score_r2):X_r2, (num_feature_r3, f1_score_r3):X_r3 }
            num_feature_and_accuracy_for_3_candidate_sol = [[num_feature_r1, f1_score_r1], [num_feature_r2, f1_score_r2], [num_feature_r3, f1_score_r3]]
            
            res, smallest_key = nds(num_feature_and_accuracy_for_3_candidate_sol)
            res_smallest_key = res[smallest_key]
            
            res_smallest_key = sorted(res_smallest_key, key=lambda x:x[1], reverse = False)
            round_robin_flag = round_robin_flag + 1
            
            if(res_smallest_key[0] + res_smallest_key[0] != 0):
                X_best_t = res_smallest_key[0]
            else:
                X_best_t = res_smallest_key[1]
            
            removed_ = Dict_vector_cardinality_accuracy[tuple(X_best_t)]
            
            Dict_vector_cardinality_accuracy_after_removing_best = Dict_vector_cardinality_accuracy.copy()
            Dict_vector_cardinality_accuracy_after_removing_best.pop(tuple(X_best_t))
            
            list_of_Dict_vector_cardinality_accuracy_after_removing_best = list(Dict_vector_cardinality_accuracy_after_removing_best.items())
            
            if(len(list_of_Dict_vector_cardinality_accuracy_after_removing_best) == 0):
                X_r1_new = Dict_vector_cardinality_accuracy[tuple(X_best_t)]
                X_r2_new = Dict_vector_cardinality_accuracy[tuple(X_best_t)]
            elif(len(list_of_Dict_vector_cardinality_accuracy_after_removing_best) == 1):
                X_r1_new = list_of_Dict_vector_cardinality_accuracy_after_removing_best[0][1]
                X_r2_new = list_of_Dict_vector_cardinality_accuracy_after_removing_best[0][1]
            else:
                X_r1_new = list_of_Dict_vector_cardinality_accuracy_after_removing_best[0][1]
                X_r2_new = list_of_Dict_vector_cardinality_accuracy_after_removing_best[1][1]
                
            base_vector = Dict_vector_cardinality_accuracy[tuple(X_best_t)]
            X_i = P_0[i-1]
            
            X_ri, num_feature_ri, f1_score_ri = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = X_i)
            X_rbase, num_feature_rbase, f1_score_rbase = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = base_vector)
            
            xi_dominates_base, base_dominates_xi, base_and_xi_are_nondominating = dc(point1=[num_feature_rbase, f1_score_rbase], point2 =[num_feature_ri, f1_score_ri])
            
            X_r1_for_xor = X_r1_new.copy()
            X_r2_for_xor = X_r2_new.copy()
            
            sigma = 0.01
            c_i = [0]*num_feature
            v_i = [0]*num_feature
            F=0.1
            random.seed(t+30*i)
            random_val = random.sample(range(0,100), 1)
            random_value = random_val[0]/100
            
            if(base_dominates_xi == True):
                c_i = [sigma]*num_feature
            else:
                for i in range(num_feature):
                    c_i[i] = min(1, (F*int((bool(X_r1_for_xor[i]) ^ bool(X_r2_for_xor[i])))+sigma))
            mu = math.exp(-math.sqrt(t)) #t is generation count
            
            #for i in range(num_feature):
            #    v_i[i] = mu * (math.floor((X_r1[i] + X_r2[i] + X_r3[i])/1.5)) + (1-mu) *((base_vector[i] * int(bool(X_r1_new[i]) ^ bool(X_r2_new[i]))) + (int(not(bool(base_vector[i]))) * int(bool(X_r1_new[i]) & bool(X_r2_new[i]))))
            #    if(v_i[i] < 0.5):
            #        v_i[i] = 0
            #    else:
            #        v_i[i] = 1
                    
            for i in range(num_feature):
                if c_i[i] < random_value:
                    v_i[i] = base_vector[i]
                else:
                    v_i[i] = 1-base_vector[i]
                
            if sum(v_i)>0:
                pass
            else:
                v_i = base_vector
                
            random.seed(t+30*i)

            u_0_1 = random.sample(range(0,100), 1)[0]
            u_0_1 = u_0_1/100

            random.seed(t+30*i)
            h=random.sample(range(0,N),1)[0]
            cr=0.5
            u_i = [0]*num_feature
                
            for i in range(num_feature):
                if(u_0_1 < cr or i==h):
                    u_i[i] = v_i[i]
                else:
                    u_i[i] = X_i[i]
                        
            X_ui, num_feature_ui, f1_score_ui = error(dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, X_rn = u_i)
            xi_dominates_ui, ui_dominates_xi, ui_and_xi_are_nondominating = dc(point1=[num_feature_ui, f1_score_ui], point2 =[num_feature_ri, f1_score_ri])

            if(xi_dominates_ui == 1):
                print("xi_dominates_ui")
                P_t_plus_1_vector_fitness.append([X_ri, num_feature_ri, f1_score_ri])
            elif(ui_dominates_xi == 1):
                print("ui_dominates_xi")
                P_t_plus_1_vector_fitness.append([X_ui, num_feature_ui, f1_score_ui])
            else:
                print("xi ui nondominating")
                P_t_plus_1_vector_fitness.append([X_ri, num_feature_ri, f1_score_ri])
                P_t_plus_1_vector_fitness.append([X_ui, num_feature_ui, f1_score_ui])
        
        print("P_t_plus_1_vector_fitnessP_t_plus_1_vector_fitnessP_t_plus_1_vector_fitnessP_t_plus_1_vector_fitness")
        print(P_t_plus_1_vector_fitness)
        
        #Remove duplicates
        P_t_plus_1_vector_fitness_unique=[]
        for i in P_t_plus_1_vector_fitness:
            if i not in P_t_plus_1_vector_fitness_unique:
                P_t_plus_1_vector_fitness_unique.append(i)
                
        dup_count = len(P_t_plus_1_vector_fitness) - len(P_t_plus_1_vector_fitness_unique)
        #print(dup_count)
        
        print("P_t_plus_1_vector_fitness")
        print(P_t_plus_1_vector_fitness)
        print("P_t_plus_1_vector_fitness_unique")
        print(P_t_plus_1_vector_fitness_unique)
        
        P_t_plus_1_vector_fitness = P_t_plus_1_vector_fitness_unique.copy()
        
        if(gen_max/(obps_freq+1) == math.ceil(gen_max/(obps_freq+1))):
            top_front_ = top_front(P_t_plus_1_vector_fitness=P_t_plus_1_vector_fitness)
            print("top_front_")
            print(top_front_)
            optimal_sol_, optimal_sol_fitness_ = optimal_sol(P_t_plus_1_vector_fitness=P_t_plus_1_vector_fitness)
            obps_result = obps(X_train, X_test, y_train, y_test, S=top_front_, optimal_sol = optimal_sol_)
                        
            to_be_removed_sol = optimal_sol_.copy()
            to_be_removed_fit = optimal_sol_fitness_.copy()
                       
            to_be_removed_sol = [to_be_removed_sol, to_be_removed_fit[0], to_be_removed_fit[1]]
            
            P_t_plus_1_vector_fitness.remove(to_be_removed_sol)
            P_t_plus_1_vector_fitness.append(obps_result[0])
        print("vedP_t_plus_1_vector_fitness")
        print(P_t_plus_1_vector_fitness)
        print("len of P_t_plus_1_vector_fitness")
        print(len(P_t_plus_1_vector_fitness))
        print(N)
        if len(P_t_plus_1_vector_fitness) > N:
            population_for_next_gen_ = select_population_for_next_gen(population_size=N, P_t_plus_1_vector_fitness=P_t_plus_1_vector_fitness)
        else:
            population_for_next_gen_ = P_t_plus_1_vector_fitness
        
        print("population_for_next_gen_population_for_next_gen_")
        print(population_for_next_gen_)
        all_gen_population_and_fitness.append(population_for_next_gen_)
        
        P_0 = list(map(itemgetter(0), population_for_next_gen_))
        
        if (len(P_0) < 3):
            print(f"stopped due to pupulation having size less than 3, i.e., size of {len(P_0)}")
            break
        
        print("Checking for convergence starts")
        P_0_metric = list(map(itemgetter(1,2), population_for_next_gen_))
        ind = HV(ref_point=ref_point)
        #print("HV for gen" + str(i+1), ind(np.array(P_0_metric)))
        HV_list.append(ind(np.array(P_0_metric)))
        print("HV_list till now is ")
        print(HV_list)
        
        
        #for i in range(len(HV_list)):
        if len(HV_list) > 10:
            i = len(HV_list)-1
            print(f"HV list has {i+1} elements now")
            mean_hv_of_prev_10_gen = statistics.mean(HV_list[i-10:i])
            print(f"mean_hv_of_prev_10_gen {mean_hv_of_prev_10_gen}")
            difference_of_current_hv_and_mean_last_10_gen = HV_list[i] - mean_hv_of_prev_10_gen
            print(f"difference_of_current_hv_and_mean_last_10_gen {difference_of_current_hv_and_mean_last_10_gen}")

            mean_hv_of_prev_10_gen_list.append(mean_hv_of_prev_10_gen)
            difference_of_current_hv_and_mean_last_10_gen_list.append(difference_of_current_hv_and_mean_last_10_gen)

            print("mean_hv_of_prev_10_gen_list")
            print(mean_hv_of_prev_10_gen_list)
            print("difference_of_current_hv_and_mean_last_10_gen_list")
            print(difference_of_current_hv_and_mean_last_10_gen_list)
            
            if(len(difference_of_current_hv_and_mean_last_10_gen_list)>=10):
                j=len(difference_of_current_hv_and_mean_last_10_gen_list)
                if(sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])<=0):
                    print(f"at gen {i+1} sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j]) is less than zero, i.e., {sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])}")
                    print("difference_of_current_hv_and_mean_last_10_gen_list[j-10:j]")
                    print(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])
                    converged = True
                    print("converged is true now")
                    break
                else:
                    print(f"at gen {i+1} sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j]) is NOT less than zero, i.e., {sum(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])}")
                    print("difference_of_current_hv_and_mean_last_10_gen_list[j-10:j]")
                    print(difference_of_current_hv_and_mean_last_10_gen_list[j-10:j])
                    print(f"at gen {i+1} is is not converged")
                    continue
            print("Checking for convergence ends")
                    
        if (converged == True):
            break
        
    return P_t_plus_1_vector_fitness, all_gen_population_and_fitness

In [37]:
import numpy as np
import random
Feature_population = []
rng = np.random.default_rng(23) #number of features
for i in range(50): #number of candidate solution in initial population
    array_of_0_1 = rng.random(23) #number of features
    array_of_0_1[array_of_0_1>=0.5] = 1
    array_of_0_1[array_of_0_1<0.5] = 0
    array_of_0_1=array_of_0_1.astype(int)
    list_of_0_1 = list(array_of_0_1)
    
    Feature_population.append(list_of_0_1)

In [38]:
len(Feature_population)

50

In [39]:
print(Feature_population)

[[1, 1, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 0, 1, 1], [1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 1], [1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 1, 0], [0, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0], [1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1], [0, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 1], [0, 0, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 0], [1, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1], [0, 0, 1, 1, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 0, 1, 1, 1], [0, 1, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1], [1, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1], [0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1], [0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0], [1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 1, 1, 0, 1, 1, 0, 0], [0, 1

In [40]:
last_gen_vector_fitness, all_generation_population_and_fitness = MOFS(gen_max=100, obps_freq=1, dataset_train=X_train, target_train = y_train, dataset_test = X_test, target_test = y_test, initial_population = Feature_population)

Attention - Generation 1 starts
NNNNNNNNNNNNNNNNNNNNNN
50
34 18 39
[1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 0, 0, 1, 1, 0, 0] [0, 0, 0, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 0, 1] [0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0]
f1 score is-0.2948905109489051
accuracy is0.7853333333333333
error rate is0.21466666666666667
roc suc score is0.5763566790352505
gini is0.1527133580705009
[[6664  376]
 [1556  404]]
              precision    recall  f1-score   support

           0       0.81      0.95      0.87      7040
           1       0.52      0.21      0.29      1960

    accuracy                           0.79      9000
   macro avg       0.66      0.58      0.58      9000
weighted avg       0.75      0.79      0.75      9000

f1 score is-0.36958745311967267
accuracy is0.7945555555555556
error rate is0.20544444444444443
roc suc score is0.6076545106679035
gini is0.2153090213358071
[[6609  431]
 [1418  542]]
              precision    reca

f1 score is-0.3788968824940048
accuracy is0.7985555555555556
error rate is0.20144444444444443
roc suc score is0.6122362012987013
gini is0.22447240259740253
[[6634  406]
 [1407  553]]
              precision    recall  f1-score   support

           0       0.83      0.94      0.88      7040
           1       0.58      0.28      0.38      1960

    accuracy                           0.80      9000
   macro avg       0.70      0.61      0.63      9000
weighted avg       0.77      0.80      0.77      9000

f1 score is-0.4604833442194644
accuracy is0.8164444444444444
error rate is0.18355555555555558
roc suc score is0.6516509160482374
gini is0.3033018320964749
[[6643  397]
 [1255  705]]
              precision    recall  f1-score   support

           0       0.84      0.94      0.89      7040
           1       0.64      0.36      0.46      1960

    accuracy                           0.82      9000
   macro avg       0.74      0.65      0.67      9000
weighted avg       0.80      0.82   

f1 score is-0.4376840039254171
accuracy is0.809
error rate is0.19099999999999995
roc suc score is0.6402655380333951
gini is0.2805310760667903
[[6612  428]
 [1291  669]]
              precision    recall  f1-score   support

           0       0.84      0.94      0.88      7040
           1       0.61      0.34      0.44      1960

    accuracy                           0.81      9000
   macro avg       0.72      0.64      0.66      9000
weighted avg       0.79      0.81      0.79      9000

f1 score is-0.4604833442194644
accuracy is0.8164444444444444
error rate is0.18355555555555558
roc suc score is0.6516509160482374
gini is0.3033018320964749
[[6643  397]
 [1255  705]]
              precision    recall  f1-score   support

           0       0.84      0.94      0.89      7040
           1       0.64      0.36      0.46      1960

    accuracy                           0.82      9000
   macro avg       0.74      0.65      0.67      9000
weighted avg       0.80      0.82      0.80      9

f1 score is-0.4432786885245902
accuracy is0.8113333333333334
error rate is0.18866666666666665
roc suc score is0.6430455705009276
gini is0.2860911410018552
[[6626  414]
 [1284  676]]
              precision    recall  f1-score   support

           0       0.84      0.94      0.89      7040
           1       0.62      0.34      0.44      1960

    accuracy                           0.81      9000
   macro avg       0.73      0.64      0.66      9000
weighted avg       0.79      0.81      0.79      9000

f1 score is-0.4432786885245902
accuracy is0.8113333333333334
error rate is0.18866666666666665
roc suc score is0.6430455705009276
gini is0.2860911410018552
[[6626  414]
 [1284  676]]
              precision    recall  f1-score   support

           0       0.84      0.94      0.89      7040
           1       0.62      0.34      0.44      1960

    accuracy                           0.81      9000
   macro avg       0.73      0.64      0.66      9000
weighted avg       0.79      0.81    

f1 score is-0.45682989690721654
accuracy is0.8126666666666666
error rate is0.18733333333333335
roc suc score is0.6499724605751391
gini is0.29994492115027827
[[6605  435]
 [1251  709]]
              precision    recall  f1-score   support

           0       0.84      0.94      0.89      7040
           1       0.62      0.36      0.46      1960

    accuracy                           0.81      9000
   macro avg       0.73      0.65      0.67      9000
weighted avg       0.79      0.81      0.79      9000

f1 score is-0.44152431011826543
accuracy is0.8111111111111111
error rate is0.18888888888888888
roc suc score is0.6421672077922079
gini is0.28433441558441586
[[6628  412]
 [1288  672]]
              precision    recall  f1-score   support

           0       0.84      0.94      0.89      7040
           1       0.62      0.34      0.44      1960

    accuracy                           0.81      9000
   macro avg       0.73      0.64      0.66      9000
weighted avg       0.79      0.81

...

              precision    recall  f1-score   support

           0       0.83      0.96      0.89      7040
           1       0.67      0.32      0.43      1960

    accuracy                           0.82      9000
   macro avg       0.75      0.64      0.66      9000
weighted avg       0.80      0.82      0.79      9000

f1 score is-0.4313861043899066
accuracy is0.8172222222222222
error rate is0.18277777777777782
roc suc score is0.637237650742115
gini is0.27447530148423005
[[6731  309]
 [1336  624]]
              precision    recall  f1-score   support

           0       0.83      0.96      0.89      7040
           1       0.67      0.32      0.43      1960

    accuracy                           0.82      9000
   macro avg       0.75      0.64      0.66      9000
weighted avg       0.80      0.82      0.79      9000

f1 score is-0.45511758860549856
accuracy is0.8172222222222222
error rate is0.18277777777777782
roc suc score is0.6488346474953618
gini is0.2976692949907236
[[6668  

              precision    recall  f1-score   support

           0       0.78      0.99      0.87      7040
           1       0.28      0.01      0.03      1960

    accuracy                           0.78      9000
   macro avg       0.53      0.50      0.45      9000
weighted avg       0.67      0.78      0.69      9000

f1 score is-0.4313861043899066
accuracy is0.8172222222222222
error rate is0.18277777777777782
roc suc score is0.637237650742115
gini is0.27447530148423005
[[6731  309]
 [1336  624]]
              precision    recall  f1-score   support

           0       0.83      0.96      0.89      7040
           1       0.67      0.32      0.43      1960

    accuracy                           0.82      9000
   macro avg       0.75      0.64      0.66      9000
weighted avg       0.80      0.82      0.79      9000

f1 score is-0.45511758860549856
accuracy is0.8172222222222222
error rate is0.18277777777777782
roc suc score is0.6488346474953618
gini is0.2976692949907236
[[6668  

gini is0.27447530148423005
[[6731  309]
 [1336  624]]
              precision    recall  f1-score   support

           0       0.83      0.96      0.89      7040
           1       0.67      0.32      0.43      1960

    accuracy                           0.82      9000
   macro avg       0.75      0.64      0.66      9000
weighted avg       0.80      0.82      0.79      9000

f1 score is-0.45511758860549856
accuracy is0.8172222222222222
error rate is0.18277777777777782
roc suc score is0.6488346474953618
gini is0.2976692949907236
[[6668  372]
 [1273  687]]
              precision    recall  f1-score   support

           0       0.84      0.95      0.89      7040
           1       0.65      0.35      0.46      1960

    accuracy                           0.82      9000
   macro avg       0.74      0.65      0.67      9000
weighted avg       0.80      0.82      0.80      9000

f1 score is-0.4596641422456371
accuracy is0.8176666666666667
error rate is0.18233333333333335
roc suc score i

f1 score is-0.4596641422456371
accuracy is0.8176666666666667
error rate is0.18233333333333335
roc suc score is0.6511436108534322
gini is0.3022872217068644
[[6661  379]
 [1262  698]]
              precision    recall  f1-score   support

           0       0.84      0.95      0.89      7040
           1       0.65      0.36      0.46      1960

    accuracy                           0.82      9000
   macro avg       0.74      0.65      0.67      9000
weighted avg       0.80      0.82      0.80      9000

f1 score is-0.4596641422456371
accuracy is0.8176666666666667
error rate is0.18233333333333335
roc suc score is0.6511436108534322
gini is0.3022872217068644
[[6661  379]
 [1262  698]]
              precision    recall  f1-score   support

           0       0.84      0.95      0.89      7040
           1       0.65      0.36      0.46      1960

    accuracy                           0.82      9000
   macro avg       0.74      0.65      0.67      9000
weighted avg       0.80      0.82    

f1 score is-0.4596641422456371
accuracy is0.8176666666666667
error rate is0.18233333333333335
roc suc score is0.6511436108534322
gini is0.3022872217068644
[[6661  379]
 [1262  698]]
              precision    recall  f1-score   support

           0       0.84      0.95      0.89      7040
           1       0.65      0.36      0.46      1960

    accuracy                           0.82      9000
   macro avg       0.74      0.65      0.67      9000
weighted avg       0.80      0.82      0.80      9000

0.002666666666666706
0.002666666666666706
0.0
f1 score is-0.4596641422456371
accuracy is0.8176666666666667
error rate is0.18233333333333335
roc suc score is0.6511436108534322
gini is0.3022872217068644
[[6661  379]
 [1262  698]]
              precision    recall  f1-score   support

           0       0.84      0.95      0.89      7040
           1       0.65      0.36      0.46      1960

    accuracy                           0.82      9000
   macro avg       0.74      0.65      0.67  

In [41]:
print(all_generation_population_and_fitness)

[[[[1, 1, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 0, 1, 1], 11, 0.18555555555555558], [[0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0], 10, 0.18866666666666665], [[0, 0, 0, 1, 0, 1, 1, 1, 1, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0], 11, 0.18477777777777782], [[1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 1, 0], 10, 0.20144444444444443], [[0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 1, 0, 1, 1, 1, 0, 1, 0, 0], 10, 0.18577777777777782], [[0, 0, 1, 0, 1, 1, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1, 0, 0, 1, 0, 0, 0, 0], 11, 0.18422222222222218], [[1, 1, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1], 13, 0.18733333333333335], [[1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 1], 14, 0.18766666666666665], [[0, 0, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0], 13, 0.18988888888888888], [[0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 0], 11, 0.2062222222222222], [[0, 0, 0, 0, 1, 0,